In [6]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import cygnus_lib as cy
import mylib as my
from scipy.optimize import curve_fit
from scipy.stats import chisquare
import scipy.stats as stats
from itertools import combinations
import math
%matplotlib inline
x_resolution = y_resolution = 2048
import os
import requests
import ROOT
import root_numpy as rtnp
ROOT.gROOT.SetBatch(True)
cy.set_atlas_style('square')
from sklearn.cluster import DBSCAN
from sklearn.preprocessing import StandardScaler


# Run selection parameters

In [9]:

runI          = [2098] # 2320, 2318, 2317
run_ped       = 2054  # 2316 #2154 
cimax         = 300
cimin         = 0 
dataSelection = 'LAB'
rescale       = 512
nsigma        = 1.5



#########################

try:
    fileoutm = ("./data/run%d_mean.h5" % (run_ped))
    m_image = cy.read_image_h5(fileoutm)
    PedOverMax = m_image[m_image > cimax].size
    print ("Pedestal mean: %.2f, sigma: %.2f, over th. (%d) %d" % 
       (m_image[m_image<cimax].mean(), 
        np.sqrt(m_image[m_image<cimax].var()), cimax,
        (m_image>cimax).sum()))
except:
    print ("No Pedestal file for run %s, run script runs-pedestals.ipynb" % run_ped)
    print ("STOP")

    
try: 
    fileouts = ("./data/run%d_sigma.h5" % (run_ped))
    s_image = cy.read_image_h5(fileouts)
    print ("Sigma mean: %.2f, sigma: %.2f, over th. (50) %d" % 
   (s_image[s_image<50].mean(), 
    np.sqrt(s_image[s_image<50].var()), 
    (s_image>50).sum()))
except:
    print ("No Sigma file for run %s, run script runs-pedestals.ipynb" % run_ped)
    print ("STOP")

#########################

th_image   = np.round(m_image + nsigma*s_image)
print ("light over Th: %.2f " % (th_image.sum()-m_image.sum()))

    
    
for nRi in range(0,len(runI)):
    try:
        print ('Download and open file: '+cy.swift_root_file(dataSelection, runI[nRi]))
        tmp_file = cy.swift_download_file(cy.swift_root_file(dataSelection, runI[nRi]))
        print ('Open file: '+tmp_file)
        f  = ROOT.TFile.Open(tmp_file);
        print ('Find Keys: '+str(len(f.GetListOfKeys())))
        pic, wfm = cy.root_TH2_name(f)
        max_image = len(pic)
        max_wfm = len(wfm)
        print ("# of Images (TH2) Files: %d " % (max_image))
        print ("# of Waveform (TH2) Files: %d " % (max_wfm))
        nImag=max_image
    except:
        print ("ERROR: No file %d" % (runI[nRi]))
        break
#     try:
#         print ('Open file: '+cy.swift_root_file(dataSelection, runI[nRi]))
#         f = ROOT.TFile.Open(cy.swift_root_file(dataSelection, runI[nRi]))

#         print ('Find Keys: '+str(len(f.GetListOfKeys())))
#         pic, wfm = cy.root_TH2_name(f)
#         max_image = len(pic)
#         max_wfm = len(wfm)
#         print ("# of Images (TH2) Files: %d " % (max_image))
#         print ("# of Waveform (TH2) Files: %d " % (max_wfm))
#         nImag=max_image
#     except:
#         print ("ERROR: No file %d" % (runI[nRi]))
#         break

    data_to_save = []
    files = ("./data/dbscan_run%d_cmin_%d_cmax_%d_rescale_%d_nsigma_%.1f_ev_%d_ped_%d.txt" % 
                     (runI[nRi], cimin, cimax, rescale, nsigma, max_image, run_ped))
    for iTr in range(0, max_image):
        if iTr % 10 == 0:
            print ('RUN: ', runI[nRi], 'Event: ', iTr)
            print (iTr, ' >> Close and re-Open: ', tmp_file)
            f.Close()
            f  = ROOT.TFile.Open(tmp_file);

        image = rtnp.hist2array(f.Get(pic[iTr])).T

        rebin_image     = cy.rebin(image-m_image, (rescale, rescale))  
        rebin_th_image  = cy.rebin((th_image-m_image), (rescale, rescale))

        edges           = (rebin_image > rebin_th_image) & (rebin_image < cimax)         
        points          = np.array(np.nonzero(edges)).T.astype(float) 
        scaler          = StandardScaler()
        X_scaled        = scaler.fit_transform(points)

        dbscan          = DBSCAN(eps=0.05, min_samples = 2)
        dbscan.fit(points)

        clusters = dbscan.fit_predict(X_scaled)

        for ic in range (min(dbscan.labels_), max(dbscan.labels_)):
            ph = 0.
            # print ("value: ", iTr, ic, dbscan.labels_[ic], min(dbscan.labels_), max(dbscan.labels_))
            yc = points[:,1][dbscan.labels_==ic]
            xc = points[:,0][dbscan.labels_==ic]
            ph, dim = cy.cluster_par(yc, xc, rebin_image)
            width, height, pearson = cy.confidence_ellipse_par(yc,xc)
            for j in range(0, dim):
                x=int(xc[j])
                y=int(yc[j])
                #ph += rebin_image[y,x]
                if j == 0:
                    x0start = x
                    y0start = y
            x0end = x
            y0end = y
            data_to_save.append([iTr, ic, dim, ph, ph/dim, 
                                 x0start, y0start, x0end, y0end, width, height, pearson])

    np.savetxt(files, data_to_save, fmt='%.10e', delimiter=" ")
    print ("out file", files)
    if not cy.rm_file(tmp_file):
        print (">> File "+tmp_file+" removed")
        


Pedestal mean: 99.57, sigma: 0.91, over th. (300) 9
Sigma mean: 2.52, sigma: 2.14, over th. (50) 7
light over Th: 15841590.89 
Download and open file: https://swift.cloud.infn.it:8080/v1/AUTH_1e60fe39fba04701aa5ffc0b97871ed8/Cygnus/Data/LAB/histograms_Run02098.root


  0.2%    7053312 / 3850135249

  0.5%   18317312 / 3850135249

  0.8%   31105024 / 3850135249

  1.1%   42549248 / 3850135249

...

RUN:  2098 Event:  450
450  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  460
460  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  470
470  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  480
480  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  490
490  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  500
500  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  510
510  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  520
520  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  530
530  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  540
540  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  550
550  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  560
560  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  570
570  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  580
580  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  590
590  >> Close and re-Open

/home/mazzitel/cygnus_lib.py:357: RuntimeWarning: invalid value encountered in sqrt
  ell_radius_y = np.sqrt(1 - pearson)


RUN:  2098 Event:  630
630  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  640
640  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  650
650  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  660
660  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  670
670  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  680
680  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  690
690  >> Close and re-Open:  ./tmp.29004.root


/home/mazzitel/cygnus_lib.py:357: RuntimeWarning: invalid value encountered in sqrt
  ell_radius_y = np.sqrt(1 - pearson)


RUN:  2098 Event:  700
700  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  710
710  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  720
720  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  730
730  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  740
740  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  750
750  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  760
760  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  770
770  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  780
780  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  790
790  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  800
800  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  810
810  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  820
820  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  830
830  >> Close and re-Open:  ./tmp.29004.root
RUN:  2098 Event:  840
840  >> Close and re-Open

In [5]:
print ('Open file: '+cy.swift_root_file(dataSelection, runI[nRi]))
f = ROOT.TFile.Open(cy.swift_root_file(dataSelection, runI[nRi]))

Open file: https://swift.cloud.infn.it:8080/v1/AUTH_1e60fe39fba04701aa5ffc0b97871ed8/Cygnus/Data/LAB/histograms_Run02277.root


Error in <TWebFile::TWebFile>: https://swift.cloud.infn.it:8080/v1/AUTH_1e60fe39fba04701aa5ffc0b97871ed8/Cygnus/Data/LAB/histograms_Run02277.root? does not exist


In [4]:
f  = ROOT.TFile.Open('https://swift.cloud.infn.it:8080/v1/AUTH_1e60fe39fba04701aa5ffc0b97871ed8/Cygnus/Data/LAB/histograms_Run02277.root');

Error in <TWebFile::TWebFile>: https://swift.cloud.infn.it:8080/v1/AUTH_1e60fe39fba04701aa5ffc0b97871ed8/Cygnus/Data/LAB/histograms_Run02277.root? does not exist
